In [111]:
import pandas as pd
import dowhy as dw
import requests

flight_data = pd.read_csv(r'Raw_data\Airline_delay_cause_data\Airline_Delay_Cause.csv')

airport_location_data = pd.read_csv(r'Raw_data\Airport_characteristic_data\airport-codes.csv')

flight_data = pd.merge(flight_data, airport_location_data,'left',left_on='airport', right_on='iata_code')

flight_data[['latitude', 'longitude']] = flight_data['coordinates'].str.split(', ', expand=True)
flight_data['latitude'] = flight_data['latitude'].astype(float)
flight_data['longitude'] = flight_data['longitude'].astype(float)
flight_data = flight_data.drop('coordinates', axis=1)

unique_loc_data = flight_data[['airport','latitude', 'longitude']].drop_duplicates()
unique_carrier_list = flight_data[['carrier']].drop_duplicates()
unique_carrier_list = unique_carrier_list.reset_index()
unique_loc_data = unique_loc_data.reset_index()

unique_loc_data = unique_loc_data.drop('index', axis=1)



In [112]:
import pandas as pd
import requests
import time

# Load airline and airport location data
flight_data = pd.read_csv(r'Raw_data\Airline_delay_cause_data\Airline_Delay_Cause.csv')
airport_location_data = pd.read_csv(r'Raw_data\Airport_characteristic_data\airport-codes.csv')

# NASA POWER API details
BASE_URL = 'https://power.larc.nasa.gov/api/temporal/monthly/point'
START_YEAR = 2013
END_YEAR = 2023
PARAMETERS = 'T2M,T2M_MAX,T2M_MIN,PRECTOTCORR,WS50M,WS50M_MAX,WS50M_MIN,FROST_DAYS,PRECSNO'

# Create a list to store weather data
weather_records = []

# Loop through each airport location
for _, row in unique_loc_data.iterrows():
    airport, lat, lon = row['airport'], row['latitude'], row['longitude']
    
    # Construct API URL
    url = f'{BASE_URL}?latitude={lat}&longitude={lon}&start={START_YEAR}&end={END_YEAR}&parameters={PARAMETERS}&community=RE&format=json'
    
    # Send request
    response = requests.get(url)
    if response.status_code == 200:
        data = response.json().get('properties', {}).get('parameter', {})
        
        # Convert API response into structured format
        for param, values in data.items():
            for date, value in values.items():
                weather_records.append({
                    'airport': airport,
                    'latitude': lat,
                    'longitude': lon,
                    'date': date,
                    'parameter': param,
                    'value': value
                })
    else:
        print(f'Failed to fetch data for {airport} (Lat: {lat}, Lon: {lon})')
    
    time.sleep(1)

# Convert to DataFrame
weather_df = pd.DataFrame(weather_records)

# Save to CSV
weather_df.to_csv(r'Mid_processing\airport_weather_data.csv', index=False)

print('Weather data saved successfully')


KeyboardInterrupt: 

In [113]:
import os
import zipfile
import pandas as pd
from collections import defaultdict

# Define directories
base_dir = r'Raw_data\Plane_ownership_data'

# Airline name mapping (dictionary for matching MASTER.txt names)
airline_mapping = {
    'Endeavor Air Inc.': ['DELTA AIR LINES INC'],
    'American Airlines Inc.': ['AMERICAN AIRLINES INC'],
    'Alaska Airlines Inc.': ['ALASKA AIRLINES INC'],
    'JetBlue Airways': ['JETBLUE AIRWAYS CORP'],
    'Delta Air Lines Inc.': ['DELTA AIR LINES INC'],
    'Frontier Airlines Inc.': ['FRONTIER AIRLINES INC', 'FRONTERA FLIGHT HOLDINGS INC'],
    'Allegiant Air': ['ALLEGIANT AIR LLC'],
    'Hawaiian Airlines Inc.': ['HAWAIIAN AIRLINES INC'],
    'Envoy Air': ['ENVOY AIR INC', 'ENVOY AIR SERVICES LLC','AMERICAN AIRLINES INC'],
    'Spirit Air Lines': ['SPIRIT AIRLINES INC'],
    'PSA Airlines Inc.': ['PSA AIRLINES INC', 'PSA MANAGEMENT AND AIRCRAFT SERVICES LLC', 'PSA LLC', 'PSA FINANCE LLC'],
    'SkyWest Airlines Inc.': ['SKYWEST AIRLINES INC'],
    'United Air Lines Inc.': ['UNITED AIRLINES INC'],
    'Southwest Airlines Co.': ['SOUTHWEST AIRLINES CO'],
    'Republic Airline': ['REPUBLIC AIRLINE INC', 'REPUBLIC AIRWAYS INC'],
    'Horizon Air': ['HORIZON AIR INDUSTRIES INC'],
    'Mesa Airlines Inc.': ['MESA AIRLINES INC'],
    'ExpressJet Airlines LLC': ['EXPRESSJET AIRLINES INC'],
    'ExpressJet Airlines Inc.': ['EXPRESSJET AIRLINES INC'],
    'Virgin America': ['VIRGIN AMERICA INC', 'VIRGIN GALACTIC VEHICLE HOLDINGS INC', 'VIRGIN BLUE LLC'],
    'US Airways Inc.': ['US AIRWAYS INC'],
    'AirTran Airways Corporation': ['AIRTRAN AIRWAYS INC'],
    'American Eagle Airlines Inc.': ['AMERICAN AIRLINES INC'],
}

# List of all airlines (for tracking results each year)
all_airlines = list(airline_mapping.keys())

# Initialize results storage
fleet_ages = defaultdict(list)

# Loop through ZIP files from 2015 to 2023
for year in range(2015, 2024):
    zip_path = os.path.join(base_dir, f'ReleasableAircraft.{year}.zip')
    
    if not os.path.exists(zip_path):
        print(f'Skipping missing file: {zip_path}')
        continue
    
    with zipfile.ZipFile(zip_path, 'r') as zip_ref:
        if 'MASTER.txt' not in zip_ref.namelist():
            print(f'MASTER.txt not found in {zip_path}')
            continue
        
        # Extract MASTER.txt
        with zip_ref.open('MASTER.txt') as file:
            df = pd.read_csv(file, delimiter=',', dtype=str)  # Read as string to avoid type issues
            
            # Standardize column names (make lowercase for consistency)
            df.columns = df.columns.str.lower()
            
            # Find correct column names dynamically
            name_col = next((col for col in df.columns if 'name' in col.lower()), None)
            year_col = next((col for col in df.columns if 'year mfr' in col.lower()), None)

            if not name_col or not year_col:
                print(f'Skipping {zip_path}: Required columns not found')
                continue

            # Keep only relevant columns
            df = df[[name_col, year_col]]
            df.dropna(inplace=True)

            # Convert Year Mfr to integer
            df[year_col] = pd.to_numeric(df[year_col], errors='coerce')
            df.dropna(inplace=True)

            # Initialize tracking for each airline
            airline_fleet_ages = {}

            # Loop through each airline and find its fleet age
            for airline, aliases in airline_mapping.items():
                df[name_col] = df[name_col].str.strip().str.upper()  # Normalize names
                airline_df = df[df[name_col].apply(lambda x: any(alias in x for alias in aliases))]
                airline_df = airline_df[(airline_df[year_col] >= 1900) & (airline_df[year_col] <= year)]

                if not airline_df.empty:
                    avg_age = (year - airline_df[year_col]).mean()  # Calculate fleet age for that year
                    airline_fleet_ages[airline] = avg_age
                else:
                    airline_fleet_ages[airline] = 'No Fleet'  # If missing, mark as No Fleet

            # Store results
            for airline, avg_age in airline_fleet_ages.items():
                fleet_ages[airline].append({'Year': year, 'Avg_Age': avg_age})

# Convert results into a DataFrame
fleet_age_df = pd.concat([pd.DataFrame(v).assign(Airline=k) for k, v in fleet_ages.items()])

#Fill No Fleet entries by either growthing last known age or, if that doesn't exist, working backward from the first available age
#Deals with cases where airline goes out of business mid-year etc.

fleet_age_df['Avg_Age'] = pd.to_numeric(fleet_age_df['Avg_Age'], errors='coerce')

print(fleet_age_df)



def fill_no_fleet(df):
    for airline in df['Airline'].unique():
        airline_data = df[df['Airline'] == airline].copy()
        
        # Fill missing 'No Fleet' values by iterating over rows
        for idx in range(1, len(airline_data)):
            if pd.isna(airline_data.iloc[idx]['Avg_Age']):
                # Find the previous available 'Avg_Age' for the airline
                prev_value = airline_data.iloc[idx - 1]['Avg_Age']
                if pd.isna(prev_value):  # Look for the first non-NaN value before 'No Fleet'
                    next_valid = airline_data[airline_data['Avg_Age'].notna()]['Avg_Age'].iloc[0]
                    airline_data.iloc[idx, airline_data.columns.get_loc('Avg_Age')] = next_valid - (len(airline_data) - idx)
                else:
                    airline_data.iloc[idx, airline_data.columns.get_loc('Avg_Age')] = prev_value + 1

        # Update the main dataframe
        merged  = pd.merge(df, airline_data, on=['Year', 'Airline'], how='left', suffixes=('_df1', '_df2'))
        merged['Avg_Age_df1'] = merged['Avg_Age_df2'].combine_first(merged['Avg_Age_df1'])
        df = merged[['Year', 'Avg_Age_df1', 'Airline']].rename(columns={'Avg_Age_df1': 'Avg_Age'})
    return df

fleet_age_df = fill_no_fleet(fleet_age_df)

# Save to CSV
output_path = r'Mid_processing\average_fleet_age.csv'
fleet_age_df.to_csv(output_path, index=False)

print(f'Fleet age data saved to {output_path}')


KeyboardInterrupt: 

In [102]:
import os
import zipfile
import pandas as pd

# Path to your folder containing the zip files
folder_path = r'Raw_data\Airline_detailed_flight_data'

# List of airport IDs you are interested in
airport_ids = unique_loc_data['airport']
carrier_ids = unique_carrier_list['carrier']


# Lists to store processed data
airport_data = []
carrier_data = []

# Process each ZIP file
for filename in os.listdir(folder_path):
    if filename.endswith('.zip'):
        zip_path = os.path.join(folder_path, filename)
        with zipfile.ZipFile(zip_path, 'r') as zip_ref:
            # Extract and read the CSV file inside
            csv_file = [f for f in zip_ref.namelist() if f.endswith('T_T100_MARKET_ALL_CARRIER.csv')][0]
            with zip_ref.open(csv_file) as my_file:
                df = pd.read_csv(my_file)
                df = df[df['DISTANCE'] > 0].copy()

                # Filter for relevant airport IDs
                df_filtered = df[(df['ORIGIN'].isin(airport_ids)) | (df['DEST'].isin(airport_ids))].copy()

                # Extract year and month
                df_filtered['year'] = df_filtered['YEAR']
                df_filtered['month'] = df_filtered['MONTH']

                # Compute Airport-Level Metrics
                airport_departures = df_filtered.groupby(['year', 'month', 'ORIGIN']).agg(
                    total_monthly_departure_flights=('PASSENGERS', 'count'),
                    total_monthly_departure_passengers=('PASSENGERS', 'sum')
                ).reset_index().rename(columns={'ORIGIN': 'airport'})

                airport_arrivals = df_filtered.groupby(['year', 'month', 'DEST']).agg(
                    total_monthly_arrival_flights=('PASSENGERS', 'count'),
                    total_monthly_arrival_passengers=('PASSENGERS', 'sum')
                ).reset_index().rename(columns={'DEST': 'airport'})

                # Merge arrival and departure data
                airport_combined = pd.merge(airport_departures, airport_arrivals, on=['year', 'month', 'airport'], how='outer').fillna(0)
                airport_data.append(airport_combined)

                # Compute Carrier-Level Metrics
                for carrier in carrier_ids:
                    carrier_df = df_filtered[df_filtered['UNIQUE_CARRIER'] == carrier].copy()
                    carrier_df['avg_distance'] = carrier_df['DISTANCE']

                    carrier_metrics = carrier_df.groupby(['year', 'month', 'UNIQUE_CARRIER', 'DEST']).agg(
                        monthly_flights=('PASSENGERS', 'count'),
                        monthly_total_passengers=('PASSENGERS', 'sum'),
                        monthly_average_flight_length=('avg_distance', 'mean')
                    ).reset_index().rename(columns={'UNIQUE_CARRIER': 'carrier', 'DEST': 'destination'})

                    carrier_data.append(carrier_metrics)

# Combine all collected data
airport_final_df = pd.concat(airport_data, ignore_index=True)
carrier_final_df = pd.concat(carrier_data, ignore_index=True)

# **Final Filtering to Keep Only Relevant Airports**
airport_final_df = airport_final_df[airport_final_df['airport'].isin(airport_ids)]
carrier_final_df = carrier_final_df[carrier_final_df['destination'].isin(airport_ids)]

# Save the final filtered data to CSV
airport_output_path = r'Mid_processing\airport_flight_data.csv'
carrier_output_path = r'Mid_processing\carrier_flight_data.csv'

airport_final_df.to_csv(airport_output_path, index=False)
carrier_final_df.to_csv(carrier_output_path, index=False)

print('Filtered airport data saved to:', airport_output_path)
print('Filtered carrier data saved to:', carrier_output_path)




Filtered airport data saved to: Mid_processing\airport_flight_data.csv
Filtered carrier data saved to: Mid_processing\carrier_flight_data.csv


In [103]:
import os
import pandas as pd
from io import StringIO

# Folder containing employee data files
folder_path = r'Raw_data\Airline_employee_data'

# Initialize list to store processed data
all_data = []

# Loop through all files in the folder
for filename in os.listdir(folder_path):
    if filename.startswith("Employees_By_Month") and filename.endswith(".xls"):
        file_path = os.path.join(folder_path, filename)

        # Extract airline code from filename (e.g., Employees_By_Month(9E).xls -> 9E)
        airline_code = filename.split("(")[-1].split(")")[0]

        # Read the raw file content
        with open(file_path, "r", encoding="utf-8") as file:
            html_content = file.read()

        # **Use StringIO to wrap the HTML content before reading it with pandas**
        tables = pd.read_html(StringIO(html_content))

        # Assuming relevant data is in the first table
        df = tables[0]

        # Rename columns to match the required format
        df.columns = ["month", "year", "full_time", "part_time", "grand_total"]

        # Add airline column
        df["carrier"] = airline_code

        # Append to list
        all_data.append(df)

# Combine all data into a single DataFrame
final_df = pd.concat(all_data, ignore_index=True)

# Save the result to CSV
output_path = r'Mid_processing\aggregated_employee_data.csv'
final_df.to_csv(output_path, index=False)

print("Employee data successfully processed and saved to:", output_path)


Employee data successfully processed and saved to: Mid_processing\aggregated_employee_data.csv


In [104]:
import pandas as pd

# Load the runways data
runways_df = pd.read_csv(r'Raw_data\Airport_characteristic_data\runways.csv')
airport_location_data = pd.read_csv(r'Raw_data\Airport_characteristic_data\airport-codes.csv')

# List of airports
runway_ids = pd.merge(unique_loc_data, airport_location_data, how='left', left_on='airport', right_on='iata_code')
runway_ids = pd.merge(runway_ids, runways_df, how='left', left_on='ident', right_on='airport_ident')

# Count the number of runways per airport
runway_counts = runway_ids.groupby("airport").size().reset_index(name="number_of_runways")

# Save the result to a new CSV
runway_counts.to_csv(r"Mid_processing\airport_runway_counts.csv", index=False)

print("CSV with runway counts generated successfully!")


CSV with runway counts generated successfully!


In [105]:
import shutil

shutil.copy(r'Raw_data\Airline_delay_cause_data\Airline_Delay_Cause.csv', r'Mid_processing\Airline_Delay_Cause.csv')
shutil.copy(r'Raw_data\Airport_characteristic_data\airport-codes.csv',r'Mid_processing\airport-codes.csv')

'Mid_processing\\airport-codes.csv'

In [ ]:
import pandas as pd

# Define the folder path
folder_path = "Mid_processing"

# Step 1: Load 'Airline_Delay_Cause.csv'
df = pd.read_csv(f"{folder_path}/Airline_Delay_Cause.csv")

# Step 2: Load 'aggregated_employee_data.csv' and merge
employee_df = pd.read_csv(f"{folder_path}/aggregated_employee_data.csv")[["year", "month", "carrier", "grand_total"]]
employee_df.rename(columns={"grand_total": "carrier_employees"}, inplace=True)
df = df.merge(employee_df, on=["year", "month", "carrier"], how="left")

# Step 3: Load 'airport_flight_data.csv' and merge
airport_flight_df = pd.read_csv(f"{folder_path}/airport_flight_data.csv")
airport_flight_df.rename(columns={
    "total_monthly_departure_flights": "airport_total_monthly_departure_flights",
    "total_monthly_departure_passengers": "airport_total_monthly_departure_passengers",
    "total_monthly_arrival_flights": "airport_total_monthly_arrival_flights",
    "total_monthly_arrival_passengers": "airport_total_monthly_arrival_passengers"
}, inplace=True)
df = df.merge(airport_flight_df, on=["year", "month", "airport"], how="left")

# Step 4: Load 'airport_runway_count.csv' and merge
runway_df = pd.read_csv(f"{folder_path}/airport_runway_counts.csv")
runway_df.rename(columns={"number_of_runways": "no_airport_runways"}, inplace=True)
df = df.merge(runway_df, on="airport", how="left")

# Step 5: Load 'airport_weather_data.csv' and pivot parameters
weather_df = pd.read_csv(f"{folder_path}/airport_weather_data.csv")
weather_df["year"] = weather_df["date"].astype(str).str[:4].astype(int)
weather_df["month"] = weather_df["date"].astype(str).str[4:6].astype(int)
weather_df.drop(columns=["date"], inplace=True)
weather_df = weather_df.pivot_table(index=["airport", "year", "month"], columns="parameter", values="value").reset_index()
df = df.merge(weather_df, on=["airport", "year", "month"], how="left")

# Step 6: Load 'airport-codes.csv' and merge, keeping only 'type'
airport_codes_df = pd.read_csv(f"{folder_path}/airport-codes.csv")[["iata_code", "type", "coordinates"]]

# Extract the latitude (first value in the "coordinates" column)
airport_codes_df["latitude"] = airport_codes_df["coordinates"].str.split(", ").str[0].astype(float)

# Drop the original "coordinates" column
airport_codes_df = airport_codes_df.drop(columns=["coordinates"])
df = df.merge(airport_codes_df, left_on="airport", right_on="iata_code", how="left").drop(columns=["iata_code"])

# Step 7: Load 'average_fleet_age.csv' and merge
fleet_age_df = pd.read_csv(f"{folder_path}/average_fleet_age.csv")
fleet_age_df.rename(columns={"Avg_Age": "aircraft_fleet_average_age"}, inplace=True)
df = df.merge(fleet_age_df, left_on=["year", "carrier_name"], right_on=["Year", "Airline"], how="left").drop(columns=["Year", "Airline"])

# Step 8: Load 'carrier_flight_data.csv' and merge
carrier_flight_df = pd.read_csv(f"{folder_path}/carrier_flight_data.csv")
carrier_flight_df.rename(columns={
    "monthly_flights": "monthly_flights_by_carrier_to_airport",
    "monthly_total_passengers": "monthly_total_passenger_by_carrier_to_airport",
    "monthly_average_flight_length": "monthly_average_flight_length_by_carrier_to_airport"
}, inplace=True)
df = df.merge(carrier_flight_df, left_on=["year", "month", "carrier", "airport"], right_on=["year", "month", "carrier", "destination"], how="left").drop(columns=["destination"])



#Rename for legibility/consistency

rename_dict = {
    'latitude': 'Latitude',
    'year': 'Year',
    'month': 'Month',
    'carrier': 'Carrier',
    'carrier_name': 'Carrier Name',
    'airport': 'Airport',
    'airport_name': 'Airport Name',
    'arr_flights': 'Arriving Flights',
    'arr_del15': 'Arriving Delayed >15 min',
    'carrier_ct': 'Carrier Delay Cause Count',
    'weather_ct': 'Weather Delay Cause Count',
    'nas_ct': 'NAS Delay Cause Count',
    'security_ct': 'Security Delay Cause Count',
    'late_aircraft_ct': 'Late Aircraft Delay Cause Count',
    'arr_cancelled': 'Arriving Cancelled',
    'arr_diverted': 'Arriving Diverted',
    'arr_delay': 'Arriving Delay',
    'carrier_delay': 'Carrier Delay',
    'weather_delay': 'Weather Delay',
    'nas_delay': 'NAS Delay',
    'security_delay': 'Security Delay',
    'late_aircraft_delay': 'Late Aircraft Delay',
    'carrier_employees': 'Carrier Employees',
    'airport_total_monthly_departure_flights': 'Airport Total Monthly Departure Flights',
    'airport_total_monthly_departure_passengers': 'Airport Total Monthly Departure Passengers',
    'airport_total_monthly_arrival_flights': 'Airport Total Monthly Arrival Flights',
    'airport_total_monthly_arrival_passengers': 'Airport Total Monthly Arrival Passengers',
    'no_airport_runways': 'No. Airport Runways',
    'FROST_DAYS': 'Frost Days',
    'PRECSNO': 'Snow Precipitation',
    'PRECTOTCORR': 'Corrected Total Precipitation',
    'T2M': 'Temperature (2m Average)',
    'T2M_MAX': 'Temperature Max (2m)',
    'T2M_MIN': 'Temperature Min (2m)',
    'WS50M': 'Wind Speed (50m Average)',
    'WS50M_MAX': 'Wind Speed Max (50m)',
    'WS50M_MIN': 'Wind Speed Min (50m)',
    'type': 'Airport Category',
    'aircraft_fleet_average_age': 'Airline Fleet Average Age',
    'monthly_flights_by_carrier_to_airport': 'Monthly Flights by Carrier to Airport',
    'monthly_total_passenger_by_carrier_to_airport': 'Monthly Total Passengers by Carrier to Airport',
    'monthly_average_flight_length_by_carrier_to_airport': 'Monthly Average Flight Length by Carrier to Airport'
}

df.rename(columns=rename_dict, inplace=True)

df['Monthly Average Passengers per Flight by Carrier to Airport'] = df['Monthly Total Passengers by Carrier to Airport']/df['Monthly Flights by Carrier to Airport']
df['Average Arrival Delay per Flight'] = df['Arriving Delay']/df['Arriving Flights']
# List of delay columns (sub-sources of delay)
delay_columns = ['Weather Delay', 'Carrier Delay', 'NAS Delay', 'Security Delay', 'Late Aircraft Delay']

# Iterate through each delay column and create a new column for average delay per flight
for delay in delay_columns:
    df[f'Average {delay} per Flight'] = df[delay] / df['Arriving Flights']

# Group by 'Carrier' and sum the 'Monthly Flights by Carrier to Airport' for each carrier
monthly_flights_by_carrier = df.groupby('Carrier')['Monthly Flights by Carrier to Airport'].sum().reset_index()

# Rename the aggregated column for clarity
monthly_flights_by_carrier.rename(columns={'Monthly Flights by Carrier to Airport': 'Monthly Flights by Carrier'}, inplace=True)

# Merge the aggregated total flights per carrier back into the original DataFrame
df = df.merge(monthly_flights_by_carrier[['Carrier', 'Monthly Flights by Carrier']], on='Carrier', how='left')


#Save final output

df.to_csv(r'Output_data\causal_model_data.csv', index=False)

print("Causal model data saved successfully!")



Causal model data saved successfully!


In [4]:
import pandas as pd
import networkx as nx
from dowhy import CausalModel
import matplotlib.pyplot as plt
import numpy as np
import statsmodels.api as sm
from dowhy import CausalModel
import pandas as pd


causal_model_data = pd.read_csv(r'Output_data\causal_model_data.csv')

# Define Directed Acyclic Graph
variables_weather = [
    "Average Weather Delay per Flight", "Frost Days", "Snow Precipitation", 
    "Corrected Total Precipitation", "Temperature Max (2m)", "Temperature Min (2m)", 
    "Wind Speed (50m Average)", "Wind Speed Max (50m)", 
    'No. Airport Runways','Latitude','Airport','Months Away From June', 'Arriving Cancelled'
]

variables_to_test = [
    "Frost Days", "Snow Precipitation", "Corrected Total Precipitation", 
    "Temperature Max (2m)", "Temperature Min (2m)", "Wind Speed (50m Average)", 
    "Wind Speed Max (50m)"
]

output_variable = "Arriving Cancelled"

causal_model_weather_data = causal_model_data[variables_weather]
causal_model_weather_data = causal_model_weather_data.dropna()

causal_graph_weather = nx.DiGraph()
causal_graph_weather.add_nodes_from(variables_weather)

edges = [
    ("Frost Days", output_variable),
    ("Snow Precipitation", output_variable),
    ("Corrected Total Precipitation", output_variable),
    ("Temperature Max (2m)", output_variable),
    ("Temperature Min (2m)", output_variable),
    ("Wind Speed (50m Average)", output_variable),
    ("Wind Speed Max (50m)", output_variable),
    # ("Latitude", "Frost Days"),
    # ("Latitude", "Snow Precipitation"),
    # ("Latitude", "Corrected Total Precipitation"),
    # ("Latitude", "Temperature Max (2m)"),
    # ("Latitude", "Temperature Min (2m)"),
    # ("Latitude", "Wind Speed (50m Average)"),
    # ("Latitude", "Wind Speed Max (50m)"),
    # ("Months Away From June", "Frost Days"),
    # ("Months Away From June", "Snow Precipitation"),
    # ("Months Away From June", "Corrected Total Precipitation"),
    # ("Months Away From June", "Temperature Max (2m)"),
    # ("Months Away From June", "Temperature Min (2m)"),
    # ("Months Away From June", "Wind Speed (50m Average)"),
    # ("Months Away From June", "Wind Speed Max (50m)")
]

causal_graph_weather.add_edges_from(edges)

# Create an empty DataFrame to store results
log_results = []

# Create an empty list to store refutation results
log_results = []

# Loop through each variable in the list
for var in variables_to_test:
    print(f"Running causal estimation and refutation for {var}")
    
    # Define the causal model
    causal_model = CausalModel(
        data=causal_model_weather_data,
        treatment=var,
        outcome=output_variable,
        graph=causal_graph_weather
    )

    # Identify the causal estimand
    estimand = causal_model.identify_effect()

    # Estimate the causal effect (Average Treatment Effect)
    causal_estimate = causal_model.estimate_effect(estimand, method_name="backdoor.linear_regression")

    # Conduct refutation tests
    #placebo_refuter = causal_model.refute_estimate(estimand, causal_estimate, method_name="placebo_treatment_refuter")
    #subset_refuter = causal_model.refute_estimate(estimand, causal_estimate, method_name="data_subset_refuter")
    #random_cause_refuter = causal_model.refute_estimate(estimand, causal_estimate, method_name="random_common_cause")

    # Store the results, including refutation scores
    result = {
        'Variable': var,
        'Mean Estimate': causal_estimate.value,
        'Conditional Estimates': str(causal_estimate),
        #'Placebo Refuter Score': placebo_refuter.new_effect, 
        #'Data Subset Refuter Score': subset_refuter.new_effect,
        #'Random Common Cause Refuter Score': random_cause_refuter.new_effect
    }

    # Append results
    log_results.append(result)

# Convert results into a DataFrame and save to CSV
log_df = pd.DataFrame(log_results)
log_df.to_csv(r'Output_data\causal_estimate_'+output_variable+r'.csv', index=False)

print("Causal estimate log with refutation metrics saved.")


Running causal estimation and refutation for Frost Days


c:\Users\RosenbergT\AppData\Local\Programs\Python\Python310\lib\site-packages\dowhy\causal_estimator.py:266: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  by_effect_mods = data.groupby(effect_modifier_names)
c:\Users\RosenbergT\AppData\Local\Programs\Python\Python310\lib\site-packages\dowhy\causal_estimators\regression_estimator.py:131: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  intercept_parameter = self.model.params[0]
c:\Users\RosenbergT\AppData\Local\Programs\Python\Python310\lib\site-packages\dowhy\causal_estimators\regression_estimator.py:131: FutureWarning: Series.__getitem__ treating keys as positions 

Running causal estimation and refutation for Snow Precipitation


c:\Users\RosenbergT\AppData\Local\Programs\Python\Python310\lib\site-packages\dowhy\causal_estimator.py:266: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  by_effect_mods = data.groupby(effect_modifier_names)
c:\Users\RosenbergT\AppData\Local\Programs\Python\Python310\lib\site-packages\dowhy\causal_estimators\regression_estimator.py:131: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  intercept_parameter = self.model.params[0]
c:\Users\RosenbergT\AppData\Local\Programs\Python\Python310\lib\site-packages\dowhy\causal_estimators\regression_estimator.py:131: FutureWarning: Series.__getitem__ treating keys as positions 

Running causal estimation and refutation for Corrected Total Precipitation


...

c:\Users\RosenbergT\AppData\Local\Programs\Python\Python310\lib\site-packages\dowhy\causal_estimator.py:266: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  by_effect_mods = data.groupby(effect_modifier_names)
c:\Users\RosenbergT\AppData\Local\Programs\Python\Python310\lib\site-packages\dowhy\causal_estimators\regression_estimator.py:131: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  intercept_parameter = self.model.params[0]
c:\Users\RosenbergT\AppData\Local\Programs\Python\Python310\lib\site-packages\dowhy\causal_estimators\regression_estimator.py:131: FutureWarning: Series.__getitem__ treating keys as positions 

Running causal estimation and refutation for Wind Speed Max (50m)


c:\Users\RosenbergT\AppData\Local\Programs\Python\Python310\lib\site-packages\dowhy\causal_estimator.py:266: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  by_effect_mods = data.groupby(effect_modifier_names)
c:\Users\RosenbergT\AppData\Local\Programs\Python\Python310\lib\site-packages\dowhy\causal_estimators\regression_estimator.py:131: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  intercept_parameter = self.model.params[0]
c:\Users\RosenbergT\AppData\Local\Programs\Python\Python310\lib\site-packages\dowhy\causal_estimators\regression_estimator.py:131: FutureWarning: Series.__getitem__ treating keys as positions 

Causal estimate log with refutation metrics saved.


c:\Users\RosenbergT\AppData\Local\Programs\Python\Python310\lib\site-packages\dowhy\causal_estimators\regression_estimator.py:131: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  intercept_parameter = self.model.params[0]
c:\Users\RosenbergT\AppData\Local\Programs\Python\Python310\lib\site-packages\dowhy\causal_estimators\regression_estimator.py:131: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  intercept_parameter = self.model.params[0]
c:\Users\RosenbergT\AppData\Local\Programs\Python\Python310\lib\site-packages\dowhy\causal_estimators\regression_estimator.py:131: FutureWarning: Series.__getitem__ treating keys as po

In [22]:
from sklearn.linear_model import LinearRegression
from sklearn.metrics import r2_score, mean_squared_error
import numpy as np
import pandas as pd

# Define the relevant columns
columns = ["Frost Days", "Snow Precipitation", 
           "Corrected Total Precipitation", "Temperature Max (2m)", 
           "Temperature Min (2m)", "Wind Speed (50m Average)", 
           "Wind Speed Max (50m)", 'Months Away From June', 
           "Average Weather Delay per Flight", 'Arriving Cancelled']

# Group by the "Airport" column first
results = []

for airport, group in causal_model_data.groupby('Airport'):
    # Convert columns to numeric after grouping
    group[columns] = group[columns].apply(pd.to_numeric, errors='coerce')

    # Drop rows with NaN values in the relevant columns
    group = group.dropna(subset=columns)

    # If the group is empty after dropping NaN rows, record that no data is available
    if group.empty:
        results.append({
            'Airport': airport,
            'R²': None,
            'RMSE': None,
            'Message': 'No weather data available for this airport'
        })
    else:
        try:
            # Define independent (X) and dependent (y) variables
            X = group[[
                "Frost Days", "Snow Precipitation", "Corrected Total Precipitation", 
                "Temperature Max (2m)", "Temperature Min (2m)", 
                "Wind Speed (50m Average)", "Wind Speed Max (50m)", 'Months Away From June'
            ]]
            y = group["Average Weather Delay per Flight"]

            # Fit the linear regression model
            model = LinearRegression()
            model.fit(X, y)

            # Predict values
            y_pred = model.predict(X)

            # Compute goodness-of-fit metrics: R² and RMSE
            r2 = r2_score(y, y_pred)
            rmse = np.sqrt(mean_squared_error(y, y_pred))

            # Store the results for the airport
            results.append({
                'Airport': airport,
                'R²': r2,
                'RMSE': rmse,
                'Message': 'Data processed successfully'
            })
        except Exception as e:
            # If an error occurs in the linear model, record the error message
            results.append({
                'Airport': airport,
                'R²': None,
                'RMSE': None,
                'Message': f'Error in linear modeling: {str(e)}'
            })

# Convert the results to a DataFrame
results_df = pd.DataFrame(results)

# Display the results
print(results_df)

# Save the results to a CSV file
results_df.to_csv('airport_weather_model_results.csv', index=False)




c:\Users\RosenbergT\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\metrics\_regression.py:1266: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)


    Airport        R²       RMSE                      Message
0       ABE  0.022256   7.726135  Data processed successfully
1       ABI  0.095445   2.864642  Data processed successfully
2       ABQ  0.005604   1.845894  Data processed successfully
3       ABR  0.176194   4.485354  Data processed successfully
4       ABY  0.127787   3.421326  Data processed successfully
..      ...       ...        ...                          ...
390     XWA  0.150162  16.177802  Data processed successfully
391     YAK  0.229869   0.552655  Data processed successfully
392     YKM  0.604388   2.325096  Data processed successfully
393     YNG       NaN   0.000000  Data processed successfully
394     YUM  0.017437   1.074091  Data processed successfully

[395 rows x 4 columns]


c:\Users\RosenbergT\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\metrics\_regression.py:1266: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)


In [ ]:
# This version of edges was far too busy/complex to be useful, but is kept for reference

# edges = [

#     # Edges from Airport to weather-related variables
#     # ("Airport", "Frost Days"),
#     # ("Airport", "Snow Precipitation"),
#     # ("Airport", "Corrected Total Precipitation"),
#     # ("Airport", "Temperature (2m Average)"),
#     # ("Airport", "Temperature Max (2m)"),
#     # ("Airport", "Temperature Min (2m)"),
#     # ("Airport", "Wind Speed (50m Average)"),
#     # ("Airport", "Wind Speed Max (50m)"),
#     # ("Airport", "Wind Speed Min (50m)"),

#     # # Edges from weather variables to Weather Delay
#     # ("Frost Days", "Weather Delay"),
#     # ("Snow Precipitation", "Weather Delay"),
#     # ("Corrected Total Precipitation", "Weather Delay"),
#     # ("Temperature (2m Average)", "Weather Delay"),
#     # ("Temperature Max (2m)", "Weather Delay"),
#     # ("Temperature Min (2m)", "Weather Delay"),
#     # ("Wind Speed (50m Average)", "Weather Delay"),
#     # ("Wind Speed Max (50m)", "Weather Delay"),
#     # ("Wind Speed Min (50m)", "Weather Delay"),

#     # # Edges from Airport to other variables
#     # # ("Airport", "No. Airport Runways"),
#     # # ("Airport", "Airport Category"),
#     # # ("Airport", "Airport Total Monthly Departure Flights"),
#     # # ("Airport", "Airport Total Monthly Departure Passengers"),
#     # # ("Airport", "Airport Total Monthly Arrival Flights"),
#     # # ("Airport", "Airport Total Monthly Arrival Passengers"),
#     # # ("Airport", "Monthly Flights by Carrier to Airport"),
#     # # ("Airport", "Monthly Total Passengers by Carrier to Airport"),
#     # # ("Airport", "Monthly Average Flight Length by Carrier to Airport"),
#     # # ("Airport", "Arriving Flights"),
#     # # ("Airport", "Carrier Delay"),
#     # # ("Airport", "Weather Delay"),
#     # # ("Airport", "NAS Delay"),
#     # # ("Airport", "Security Delay"),
#     # # ("Airport", "Late Aircraft Delay"),
#     # # ("Airport", "Monthly Average Passengers per Flight by Carrier to Airport"),
#     # # ("Airport", "Average Arrival Delay per Flight"),

#     # # # No. airport runways
#     # # ("No. Airport Runways", "Airport Category"),
#     # # ("No. Airport Runways", "Late Aircraft Delay"),
#     # # ("No. Airport Runways", "NAS Delay"),

#     # # # Edges from airport category
#     # # ("Airport Category", "Airport Total Monthly Departure Flights"),
#     # # ("Airport Category", "Airport Total Monthly Departure Passengers"),
#     # # ("Airport Category", "Airport Total Monthly Arrival Flights"),
#     # # ("Airport Category", "Airport Total Monthly Arrival Passengers"),
#     # # ("Airport Category", "Monthly Flights by Carrier to Airport"),
#     # # ("Airport Category", "Monthly Total Passengers by Carrier to Airport"),
#     # # ("Airport Category", "Monthly Average Flight Length by Carrier to Airport"),
#     # # ("Airport Category", "Arriving Flights"),
#     # # ("Airport Category", "Carrier Delay"),
#     # # ("Airport Category", "NAS Delay"),
#     # # ("Airport Category", "Security Delay"),
#     # # ("Airport Category", "Late Aircraft Delay"),
#     # # ("Airport Category", "Monthly Average Passengers per Flight by Carrier to Airport"),
#     # # ("Airport Category", "Average Arrival Delay per Flight"),

#     # # Edges from Carrier to other carrier-related variables
#     # # ("Carrier", "Carrier Delay"),
#     # # ("Carrier", "Carrier Employees"),
#     # # ("Carrier", "Airline Fleet Average Age"),
#     # # ("Carrier", "Monthly Flights by Carrier to Airport"),
#     # # ("Carrier", "Monthly Total Passengers by Carrier to Airport"),
#     # # ("Carrier", "Monthly Average Flight Length by Carrier to Airport"),
#     # # ("Carrier", "Arriving Flights"),
#     # # ("Carrier", "Monthly Average Passengers per Flight by Carrier to Airport"),
#     # # ("Carrier", "Average Arrival Delay per Flight"),

#     # # Edges to Carrier delay
#     # ("Carrier Employees", "Carrier Delay"),
#     # ("Airline Fleet Average Age", "Carrier Delay"),
#     # ("Monthly Flights by Carrier to Airport", "Carrier Delay"),
#     # ("Monthly Total Passengers by Carrier to Airport", "Carrier Delay"),
#     # ("Monthly Average Flight Length by Carrier to Airport", "Carrier Delay"),
#     # ("Arriving Flights", "Carrier Delay"),
#     # ("Monthly Average Passengers per Flight by Carrier to Airport", "Carrier Delay"),

#     # # Edges to Security delay
#     # ("Airport Total Monthly Departure Flights", "Security Delay"),
#     # ("Airport Total Monthly Departure Passengers", "Security Delay"),
#     # ("Airport Total Monthly Arrival Flights", "Security Delay"),
#     # ("Airport Total Monthly Arrival Passengers", "Security Delay"),
#     # ("Airport Category", "Security Delay"),
#     # ("No. Airport Runways", "Security Delay"),

#     # # Edges to NAS delay covered already

#     # # Edges to Late aircraft delay
#     # ("Carrier Delay", "Late Aircraft Delay"),
#     # ("Weather Delay", "Late Aircraft Delay"),
#     # ("NAS Delay", "Late Aircraft Delay"),
#     # ("Security Delay", "Late Aircraft Delay"),
#     # ("Airport Total Monthly Departure Flights", "Late Aircraft Delay"),
#     # ("Airport Total Monthly Departure Passengers", "Late Aircraft Delay"),
#     # ("Airport Total Monthly Arrival Flights", "Late Aircraft Delay"),
#     # ("Airport Total Monthly Arrival Passengers", "Late Aircraft Delay"),

#     # # Edges to total (arriving) delay
#     # ("Carrier Delay", "Arriving Delay"),
#     # ("Weather Delay", "Arriving Delay"),
#     # ("NAS Delay", "Arriving Delay"),
#     # ("Security Delay", "Arriving Delay"),
#     # ("Late Aircraft Delay", "Arriving Delay"),
# ]